Ca_anal

In [1]:
from IPython import get_ipython
get_ipython().run_line_magic('reset', '-sf') 

In [2]:
import pandas as pd
import glob
from dash import Dash
import dash_core_components as dcc 
import dash_html_components as html 
from dash.dependencies import Input, Output
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
import numpy as np
import os
import re
from scipy.signal import savgol_filter
from scipy.signal import find_peaks
import modules.file_folder_handler as file_folder_handler
import modules.data_transformator as data_transformator
import modules.graph_handler as graph_handler
import modules.peak_detector as peak_detector
import modules.data_uploader as data_uploader
import plotly.express as px
import plotly.io as pio
pio.renderers.default = 'notebook'

проанализируем трейсы из папки ATP_mtRCaMP_Caff_Ctrl

## Извлекаем данные в датафрейм

In [3]:
%%time
df, type_list, save_directory = file_folder_handler.file_extraction('ATP_mtRCaMP\Check_ctrl_ATP_mtRCaMP_ctrl\*.csv')
df.reset_index(inplace=True)

CPU times: total: 969 ms
Wall time: 1.02 s


In [4]:
file_folder_handler.file_folder_creator(save_directory)

'Folder created'

## Построим графики с SD

Построим графики с +/- 2SD для каждого трейса и сохраним их в виде картинок в соответствующих папках 

In [5]:
filename = df.filename.unique()

разделим наш df по типам dendro/mit/spine

In [6]:
dendro = pd.pivot_table(df, index = 'index', columns = 'filename', values = 'dendro')
dendro ['signal_type'] = 'dendro'
dendro['norm_time'] = np.arange(0, len(dendro)*0.01, 0.01)


mit = pd.pivot_table(df, index = 'index', columns = 'filename', values = 'mit')
mit ['signal_type'] = 'mit'
mit['norm_time'] = np.arange(0, len(mit)*0.01, 0.01)


spine = pd.pivot_table(df, index = 'index', columns = 'filename', values = 'spine')
spine ['signal_type'] = 'spine'
spine['norm_time'] = np.arange(0, len(spine)*0.01, 0.01)


In [7]:
fig = px.line(dendro,x='norm_time', y = dendro.columns[:-2])
fig.show()

In [8]:
fig = px.line(mit,x='norm_time', y = mit.columns[:-2])
fig.show()

In [9]:
#fig = px.line(spine,x='norm_time', y = spine.columns[:-2])
#fig.show()

## Графики наложения spine+dendro+mit и 2SD

In [10]:
all_data_wide= pd.concat([dendro,mit,spine])

In [11]:
all_data_wide.reset_index(inplace=True)

In [12]:
def sd_measure(data,data_type):
    new_df = pd.DataFrame()
    new_df[f'{data_type}_raw'] = data
    new_df[f'{data_type}_+2SD'] = data.mean() + data.std()*2
    new_df[f'{data_type}_-2SD'] = data.mean() - data.std()*2
    return new_df

In [13]:
def sd_graph_saver(data, sma_window):
    for i in data.columns[1:-2]:
        sns.set_theme(font_scale=1,context = 'notebook', style="ticks")
        mask_dendro_spine = (data['signal_type']=='dendro') | (data['signal_type']=='spine')
        mask_mit = data['signal_type']=='mit'

        f, (ax1, ax2, ax3) = plt.subplots(3, 1, figsize=(7, 5), sharex=True)


        plot1 = sns.lineplot(x=data[mask_dendro_spine]['norm_time'], 
                            y=data[mask_dendro_spine][i],
                            hue=data[mask_dendro_spine]['signal_type'],
                            data=data[mask_dendro_spine],palette='YlGn', ax=ax1)
        
        sd_dendro = data[data['signal_type']=='dendro'][i].std()*2 + data[data['signal_type']=='dendro'][i].mean()
        sd_spine = data[data['signal_type']=='spine'][i].std()*2 + data[data['signal_type']=='spine'][i].mean()

        plot1.axhline(sd_dendro, 
                            linestyle = '--',
                            color= 'palegreen')
        plot1.axhline(sd_spine, 
                            linestyle = '--', 
                            color= 'darkgreen')
        
        plot2 = sns.lineplot(x = data[mask_mit]['norm_time'], 
                    y = data[mask_mit][i],
                    hue = data[mask_mit]['signal_type'],
                    data=data[mask_mit], ax = ax2, palette='pastel')
        plot2.axhline(data[mask_mit][i].std()*2 + data[mask_mit][i].mean(), 
                        linestyle = '--',
                        color = 'skyblue')
        plot2.axhline(data[mask_mit][i].mean() - data[mask_mit][i].std()*2, 
                        linestyle = '--',
                        color = 'skyblue')
                #скользящее среднее
        
        
        sma = data[mask_mit][i].rolling(window=sma_window).mean()

        sns.lineplot(x = data[mask_mit]['norm_time'], 
                    y = data[mask_mit][i],
                    hue = data[mask_mit]['signal_type'],
                    data=data[mask_mit], ax = ax3, palette='pastel')
        
        
        plot3 = sns.lineplot(x = data[mask_mit]['norm_time'], 
                        y = sma, 
                        label=f'moving_avg_{sma_window}', 
                        dashes = False, 
                        ax=ax3)
        plot3.axhline(sma.std()*2 + sma.mean(), 
                        linestyle = '--',
                        color = 'skyblue')
        plot3.axhline(sma.mean() - sma.std()*2, 
                        linestyle = '--',
                        color = 'skyblue')

        #найдем и отметим пик
        
        x = data[data['signal_type']=='dendro'][i]
        peaks, _  = find_peaks(x, height = sd_dendro)
        if len(x[peaks[(peaks>130)&(peaks<250)]])!=0: 
            peak_time = data[data['signal_type']=='dendro']['norm_time'][peaks]
            peak_time = peak_time[(peak_time.index>130)&(peak_time.index<250)]
            plot1.plot(peak_time[x[peaks[(peaks>130)&(peaks<250)]].idxmax()], 
                    max(x[peaks[(peaks>130)&(peaks<250)]]), 
                    "x", 
                    color = sns.xkcd_rgb['dusty red'])

            plot1.vlines(peak_time[x[peaks[(peaks>130)&(peaks<250)]].idxmax()], 
                        ymin = data[mask_dendro_spine][i].min(), 
                        ymax = data[mask_dendro_spine][i].max(),
                        linestyle = '--',
                        color= sns.xkcd_rgb['blue'])

            plot1.vlines(x=1.3, 
                        ymin = data[mask_dendro_spine][i].min(), 
                        ymax = data[mask_dendro_spine][i].max(),
                        linestyle = '--',
                        color= sns.xkcd_rgb['red'])
            plot1.vlines(x=2.5, 
                        ymin = data[mask_dendro_spine][i].min(), 
                        ymax = data[mask_dendro_spine][i].max(),
                        linestyle = '--',
                        color= sns.xkcd_rgb['dusty red'])   


            plot2.vlines(peak_time[x[peaks[(peaks>130)&(peaks<250)]].idxmax()], ymin = data[mask_mit][i].min(), ymax = data[mask_mit][i].max(),
                            linestyle = '--',
                            color= sns.xkcd_rgb['blue']) 
        
        ax1.get_legend().remove()
        ax2.get_legend().remove()
        ax3.get_legend().remove()

        
        ax1.xaxis.set_major_locator(ticker.MultipleLocator(0.5))
        ax2.xaxis.set_major_locator(ticker.MultipleLocator(0.5))
        ax3.xaxis.set_major_locator(ticker.MultipleLocator(0.5))

        ax2.figure.legend(loc=1, bbox_to_anchor=(1.2, 1.0))

        plt.tight_layout()
        path = save_directory.setdefault(i.split('.')[0])
        fig_name = f'{path}/dendro_spine_mit.tif'
        plt.savefig(fig_name,bbox_inches='tight') 
        plt.rc('figure', max_open_warning = 0)
        plt.close('all')
        def excel_sd_saver():
            for_sd = pd.concat([sd_measure(data[data['signal_type']=='dendro'][i].reset_index(drop=True), 'dendro'),
                                sd_measure(data[mask_mit][i].reset_index(drop=True), 'mit'),
                                sd_measure(data[all_data_wide['signal_type']=='spine'][i].reset_index(drop=True), 'spine'),
                                sd_measure(sma.reset_index(drop=True), 'sma'),
                                data[mask_mit]['norm_time'].reset_index(drop=True)], 
                                axis = 1,
                                ignore_index = True)
            for_sd.rename(mapper={0:'dendro_raw',
                                1:'dendro+2SD',
                                2:'dendro-2SD',
                                3:'mit_raw',
                                4:'mit+2SD',
                                5:'mit-2SD',
                                6:'spine_raw',
                                7:'spine+2SD',
                                8:'spine-2SD',
                                9: f'mit_sma_step_{sma_window}',
                                10: f'mit_sma+2SD_step_{sma_window}',
                                11: f'mit_sma-2SD_step_{sma_window}',
                                12: 'norm_time'}, 
                                axis = 1, inplace=True)
            
            save_file_name = save_directory.setdefault(i.split('.')[0]).split('/')[-1]
            with pd.ExcelWriter(f'{path}/{save_file_name}_sd.xlsx') as writer:
                for_sd.to_excel(writer, sheet_name='SD', float_format="%.6f")
        excel_sd_saver()

In [14]:
#sd_graph_saver(all_data_wide, sma_window=7)

In [15]:
#for_sd = pd.concat([sd_measure(dendro.iloc[:, :-2], 'dendro'), sd_measure(mit.iloc[:, :-2], 'mit'), sd_measure(spine.iloc[:, :-2], 'spine')], axis = 1)

In [17]:
with pd.ExcelWriter('Check_ctrl_ATP_mtRCaMP_ctrl.xlsx') as writer:
    #for_sd.to_excel(writer, sheet_name='SD', float_format="%.6f")
    dendro.to_excel(writer, sheet_name='dendro', float_format="%.6f")
    mit.to_excel(writer, sheet_name='mit', float_format="%.6f")
    spine.to_excel(writer, sheet_name='spine', float_format="%.6f")